# Importing libraries


In [1]:
import requests # library to handle requests
import pandas as pd # library for data analsysis
!pip install geopandas
import geopandas
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import numpy as np # library to handle data in a vectorized manner
import random # library for random number generation

!pip install geopy
#!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim # module to convert an address into latitude and longitude values

# libraries for displaying images
from IPython.display import Image 
from IPython.core.display import HTML 

import json
# tranforming json file into a pandas dataframe library
from pandas.io.json import json_normalize

!pip install folium
#!conda install -c conda-forge folium=0.5.0 --yes
import folium # plotting library
from folium import plugins

# Matplotlib and associated plotting modules
import matplotlib as mpl # plotting package
import matplotlib.pyplot as plt 
import matplotlib.cm as cm
import matplotlib.colors as colors
%matplotlib inline
mpl.style.use(['ggplot'])

# import k-means from clustering stage
from sklearn.cluster import KMeans
!conda install -c conda-forge shapely -y #install shapely
from shapely.ops import transform
from functools import partial
from shapely.geometry import shape, GeometryCollection, Point
!pip install pyproj
import pyproj

print('Folium installed')
print('Libraries imported.')

     |████████████████████████████████| 972kB 7.8MB/s eta 0:00:01
     |████████████████████████████████| 14.7MB 2.3MB/s  eta 0:00:01               | 266kB 30.8MB/s eta 0:00:01
     |████████████████████████████████| 1.8MB 37.0MB/s eta 0:00:01
     |████████████████████████████████| 10.9MB 25.5MB/s eta 0:00:01
     |████████████████████████████████| 102kB 6.5MB/s ta 0:00:011
Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - shapely


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    geos-3.8.1                 |       he1b5a44_0         1.0 MB  conda-forge
    python_abi-3.6             |          1_cp36m           4 KB  conda-forge
    shapely-1.7.0              |   py36h3d6ee9d_3         435 KB  conda-forge
    openssl-1.1.1g             |       h516909a_1         2.1 MB  conda-forge
    certifi-2020.6.20      

# Reading a map of Poland from the json file


In [2]:
!wget -q -O 'stanford-xh662zc5620-geojson.json' https://raw.githubusercontent.com/KatH-M/Coursera_Capstone/master/stanford-xh662zc5620-geojson.json
    
with open("stanford-xh662zc5620-geojson.json") as json_data:
    Poland_data = json.load(json_data)
    neighborhoods_data = Poland_data["features"]
    
Poland_geo_coll = GeometryCollection([shape(features["geometry"]).buffer(0) for features in neighborhoods_data])

proj = partial(pyproj.transform, pyproj.Proj(init='epsg:4326'),
               pyproj.Proj(init='epsg:32633'))

Poland_geo_coll_new = transform(proj, Poland_geo_coll)
Poland_geo_coll_new

/opt/conda/envs/Python36/lib/python3.6/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))
/opt/conda/envs/Python36/lib/python3.6/site-packages/pyproj/crs/crs.py:294: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  projstring = _prepare_from_string(" ".join((projstring, projkwargs)))
/opt/conda/envs/Python36/lib/python3.6/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method.

## Data with all cities and regions of Poland.  

In [71]:
# neighborhoods_data


## Note to the reader of this project: I have decided to hide neighborhoods_data file, as it is huge and takes lots of space. If you are interested how it looks, please see the link for the previous version. https://github.com/KatH-M/Applied-Data-Science-Capstone-Project-/blob/master/Capstone_Poland_silesian_metropolia%20(3)%20(14).ipynb

## To get a data frame with names of all cities in Poland and their coordinates I run the code that parses through the json file and pulls out those names with centroid coordinates and geometries of the polygons. 

In [6]:
region = []
Neighborhood = []
centroidx = []
centroidy = []
geometry = []

i = 0
while(i != len(neighborhoods_data)):
    region.append(neighborhoods_data[i]['properties']['name_1'])
    Neighborhood.append(neighborhoods_data[i]['properties']['name_2'])
    mypoly = shape(neighborhoods_data[i]['geometry'])
    centroidx.append(mypoly.centroid.x)
    centroidy.append(mypoly.centroid.y)
    geometry.append(neighborhoods_data[i]['geometry'])
    i = i + 1
    


In [7]:
Poland_df = pd.DataFrame(columns=['region', 'Neighborhood','centroid_x', 'centroid_y', 'coordinates'])

Poland_df['region'] = region
Poland_df['Neighborhood'] = Neighborhood
Poland_df['centroid_x'] = centroidx
Poland_df['centroid_y'] = centroidy
Poland_df['coordinates'] = geometry

Poland_df.head()

region Neighborhood  centroid_x  centroid_y  \
0   Łódź    Łódź East   19.643637   51.631088   
1   Łódź         Łódź   19.456616   51.722929   
2   Łódź         Łask   19.030262   51.477072   
3   Łódź      Łęczyca   19.167463   52.053711   
4   Łódź       Łowicz   19.860785   52.073348   

                                         coordinates  
0  {'type': 'MultiPolygon', 'coordinates': [[[[19...  
1  {'type': 'MultiPolygon', 'coordinates': [[[[19...  
2  {'type': 'MultiPolygon', 'coordinates': [[[[18...  
3  {'type': 'MultiPolygon', 'coordinates': [[[[19...  
4  {'type': 'MultiPolygon', 'coordinates': [[[[19...

In [8]:
print('The dataframe of Poland has {} regions called voivodeship and {} neighborhoods known as cities and districts.'.format(
        len(Poland_df['region'].unique()),
       Poland_df.shape[0]
    )
)

The dataframe of Poland has 16 regions called voivodeship and 376 neighborhoods known as cities and districts.


### We are interested to know how many neighborhoods (cities and districts) are in the Silesian voivodeship only. I need to get all cities and districts belonging to this region, together with their corresponding coordinates in a data frame format.

In [9]:
Silesian_neigh = Poland_df.loc[Poland_df['region'] == 'Silesian'].reset_index(drop=True)

In [10]:
Silesian_neigh



region          Neighborhood  centroid_x  centroid_y  \
0   Silesian                  Żory   18.685270   50.022560   
1   Silesian                Żywiec   19.184707   49.587275   
2   Silesian        Świętochłowice   18.826438   50.235390   
3   Silesian                Będzin   19.116783   50.371653   
4   Silesian         Bielsko-Biała   19.058871   49.791412   
5   Silesian               Bielsko   19.046777   49.804282   
6   Silesian        Bieruń-Lędziny   19.153136   50.052411   
7   Silesian                 Bytom   18.847702   50.322524   
8   Silesian               Chorzów   18.877021   50.256611   
9   Silesian               Cieszyn   18.811055   49.731717   
10  Silesian      Częstochowa City   19.108907   50.765166   
11  Silesian           Częstochowa   19.362686   50.761963   
12  Silesian      Dąbrowa Górnicza   19.278621   50.305332   
13  Silesian          Gliwice City   18.617840   50.273288   
14  Silesian               Gliwice   18.501074   50.333499   
15  Silesian      Jastrzębie-Zdrój   18.614513   49.950146   
16  Silesian              Jaworzno   19.283292   50.175453   
17  Silesian               Kłobuck   18.842704   50.883408   
18  Silesian         Katowice City   18.995479   50.186151   
19  Silesian             Lubliniec   18.753959   50.629159   
20  Silesian               Mikołów   18.821696   50.109081   
21  Silesian             Mysłowice   19.147434   50.152310   
22  Silesian               Myszków   19.302124   50.565072   
23  Silesian       Piekary Śląskie   18.918126   50.335267   
24  Silesian              Pszczyna   18.888372   49.965744   
25  Silesian              Racibórz   18.219360   50.100139   
26  Silesian           Ruda Śląska   18.763319   50.207801   
27  Silesian           Rybnik City   18.516108   50.089914   
28  Silesian                Rybnik   18.534643   50.099888   
29  Silesian  Siemianowice Śląskie   18.960857   50.278223   
30  Silesian             Sosnowiec   19.184173   50.245526   
31  Silesian            Tarnowskie   18.799812   50.445403   
32  Silesian            Tychy City   19.009399   50.085994   
33  Silesian             Wodzisław   18.401856   49.985707   
34  Silesian                Zabrze   18.744917   50.275122   
35  Silesian             Zawiercie   19.618607   50.474186   

                                          coordinates  
0   {'type': 'MultiPolygon', 'coordinates': [[[[18...  
1   {'type': 'MultiPolygon', 'coordinates': [[[[19...  
2   {'type': 'MultiPolygon', 'coordinates': [[[[18...  
3   {'type': 'MultiPolygon', 'coordinates': [[[[19...  
4   {'type': 'MultiPolygon', 'coordinates': [[[[19...  
5   {'type': 'MultiPolygon', 'coordinates': [[[[19...  
6   {'type': 'MultiPolygon', 'coordinates': [[[[19...  
7   {'type': 'MultiPolygon', 'coordinates': [[[[18...  
8   {'type': 'MultiPolygon', 'coordinates': [[[[18...  
9   {'type': 'MultiPolygon', 'coordinates': [[[[18...  
10  {'type': 'MultiPolygon', 'coordinates': [[[[19...  
11  {'type': 'MultiPolygon', 'coordinates': [[[[19...  
12  {'type': 'MultiPolygon', 'coordinates': [[[[19...  
13  {'type': 'MultiPolygon', 'coordinates': [[[[18...  
14  {'type': 'MultiPolygon', 'coordinates': [[[[18...  
15  {'type': 'MultiPolygon', 'coordinates': [[[[18...  
16  {'type': 'MultiPolygon', 'coordinates': [[[[19...  
17  {'type': 'MultiPolygon', 'coordinates': [[[[19...  
18  {'type': 'MultiPolygon', 'coordinates': [[[[18...  
19  {'type': 'MultiPolygon', 'coordinates': [[[[19...  
20  {'type': 'MultiPolygon', 'coordinates': [[[[18...  
21  {'type': 'MultiPolygon', 'coordinates': [[[[19...  
22  {'type': 'MultiPolygon', 'coordinates': [[[[19...  
23  {'type': 'MultiPolygon', 'coordinates': [[[[18...  
24  {'type': 'MultiPolygon', 'coordinates': [[[[18...  
25  {'type': 'MultiPolygon', 'coordinates': [[[[18...  
26  {'type': 'MultiPolygon', 'coordinates': [[[[18...  
27  {'type': 'MultiPolygon', 'coordinates': [[[[18...  
28  {'type': 'MultiPolygon', 'coordinates': [[[[18...  
29  {'type': 'MultiPolygon', 'c

In [11]:
Silesian_neigh.Neighborhood



0                     Żory
1                   Żywiec
2           Świętochłowice
3                   Będzin
4            Bielsko-Biała
5                  Bielsko
6           Bieruń-Lędziny
7                    Bytom
8                  Chorzów
9                  Cieszyn
10        Częstochowa City
11             Częstochowa
12        Dąbrowa Górnicza
13            Gliwice City
14                 Gliwice
15        Jastrzębie-Zdrój
16                Jaworzno
17                 Kłobuck
18           Katowice City
19               Lubliniec
20                 Mikołów
21               Mysłowice
22                 Myszków
23         Piekary Śląskie
24                Pszczyna
25                Racibórz
26             Ruda Śląska
27             Rybnik City
28                  Rybnik
29    Siemianowice Śląskie
30               Sosnowiec
31              Tarnowskie
32              Tychy City
33               Wodzisław
34                  Zabrze
35               Zawiercie
Name: Neighborhood, dtype: o

In [12]:
print('The dataframe shows one voivodeship called Silesia with {} cities and districts that belong to its region.'.format(
        len(Silesian_neigh['Neighborhood'].unique()),
        Silesian_neigh.shape[0]
    )
)
  


The dataframe shows one voivodeship called Silesia with 36 cities and districts that belong to its region.


#### Please note that the data represent cities and districts hence some names are similar. Wikipedia confirms that information (there are 19 cities and 17 districts).
https://pl.wikipedia.org/wiki/Wojew%C3%B3dztwo_%C5%9Bl%C4%85skie

### Let's visualise Silesian voivodeship and its neighborhoods

In [13]:
address = 'Katowice, Poland'

geolocator = Nominatim(user_agent="foursquare_agent")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Katowice are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Katowice are 50.2598987, 19.0215852.


In [14]:
# create map of Katowice using latitude and longitude values
map_Silesia = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lon, region, Neighborhood in zip(Silesian_neigh['centroid_y'], Silesian_neigh['centroid_x'], Silesian_neigh['region'], Silesian_neigh['Neighborhood']):
    label = '{}, {}'.format(Neighborhood, region)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_Silesia)  
    
map_Silesia

## Now I am going to explore the venues in Silesia. To start with I am exploring all possible venue categores and their IDs and then after having conversation with my client I am selecting only the categories of interest to him. 

### Defining forsquare credentials

In [15]:
CLIENT_ID = "TJJA2JC1THEWW1AHB0YC4L24TWPQ4VDFOBHW0U3OEQ2MMXOR" # your Foursquare ID
CLIENT_SECRET = "KMJPEOZNJQWE5PQRD20P2NKZYORRQDCKNTTFTOEAI5IMW4CO" # your Foursquare Secret
VERSION = '20200803'
LIMIT = 100
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: TJJA2JC1THEWW1AHB0YC4L24TWPQ4VDFOBHW0U3OEQ2MMXOR
CLIENT_SECRET:KMJPEOZNJQWE5PQRD20P2NKZYORRQDCKNTTFTOEAI5IMW4CO


## Note to the reader of this project: I have decided to hide json file, as it is huge and takes lots of space. If you are interested how it looks, please see the link for the previous version. https://github.com/KatH-M/Applied-Data-Science-Capstone-Project-/blob/master/Capstone_Poland_silesian_metropolia%20(3)%20(14).ipynb¶

In [78]:
url = 'https://api.foursquare.com/v2/venues/categories?client_id={}&client_secret={}&v={}'.format(CLIENT_ID, CLIENT_SECRET, VERSION)
#url

#results = requests.get(url).json()
#json.dumps(results)

In [76]:
def getAllcategories(categoryResp):
    categoryBranch = categoryResp['categories']
    idList = []
    nameList = []
    for i,node in enumerate(categoryBranch):
        idList.append(node['id'])
        nameList.append(node['name'])
        
        if('categories' in node.keys()):
            subDict = getAllcategories(node)
            
        idList.extend(subDict['id'])
        nameList.extend(subDict['name'])
    
    category_list = {'id':idList,'name':nameList}
    
    return category_list

In [77]:
category_list = getAllcategories(results["response"])
all_cat_df = pd.DataFrame(category_list)
all_cat_df.head()

id                  name
0  4d4b7104d754a06370d81259  Arts & Entertainment
1  56aa371be4b08b9a8d5734db  Amphitheater        
2  4fceea171983d5d06c3e9823  Aquarium            
3  4bf58dd8d48988d1e1931735  Arcade              
4  4bf58dd8d48988d1e2931735  Art Gallery

In [19]:
all_cat_df[all_cat_df['name'].str.contains('Center')]


id                        name
85   4bf58dd8d48988d1a9941735          College Rec Center
103  4bf58dd8d48988d1ab941735              Student Center
513  4bf58dd8d48988d175941735        Gym / Fitness Center
524  590a0744340a5803fd8508c3          Weight Loss Center
579  52e81612bcbc57f1066b7a26           Recreation Center
618  56aa371be4b08b9a8d573517             Business Center
621  52e81612bcbc57f1066b7a34            Community Center
622  4bf58dd8d48988d1ff931735           Convention Center
624  52e81612bcbc57f1066b7a32             Cultural Center
626  52e81612bcbc57f1066b7a37         Distribution Center
644  4bf58dd8d48988d104941735              Medical Center
647  5f2c43a65b4c177b9a6dcc62       Blood Donation Center
661  56aa371be4b08b9a8d57351d                Rehab Center
662  56aa371be4b08b9a8d573526          Urgent Care Center
685  56aa371ce4b08b9a8d573570      Adult Education Center
702  4bf58dd8d48988d131941735            Spiritual Center
819  4eb1c0253b7b52c0e1adc2e9               Garden Center
956  4f4530164b9074f6e4fb00ff  Tourist Information Center

# Search for selected venue categories in all cities belonging to the Silesian region

In [20]:
def getNearbyVenues(Neighborhood, centroid_y, centroid_x, radius=10000, LIMIT=100):
    
    venues_list=[]
    
    radius=10000
    LIMIT=100
    categories = '56aa371be4b08b9a8d573511,52e81612bcbc57f1066b7a23,5bae9231bedf3950379f89cd,4bf58dd8d48988d161941735,4eb1d4d54b900d56c88a45fc,52e81612bcbc57f1066b7a21,52e81612bcbc57f1066b7a13,4eb1d4dd4b900d56c88a45fd,4bf58dd8d48988d1e4931735,52e81612bcbc57f1066b79ea,4bf58dd8d48988d1e6941735,58daa1558bbb0b01f18ec1b0,5032829591d4c4b30a586d5e,56aa371be4b08b9a8d573541,4bf58dd8d48988d165941735,4bf58dd8d48988d166941735,5bae9231bedf3950379f89d0,5bae9231bedf3950379f89c7,4bf58dd8d48988d1de941735'    
    for name, lat, lng in zip(Neighborhood, centroid_y, centroid_x):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&categoryId={}&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            categories,
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [21]:
location_venues = getNearbyVenues(Neighborhood=Silesian_neigh['Neighborhood'],
                                   centroid_y=Silesian_neigh['centroid_y'],
                                   centroid_x=Silesian_neigh['centroid_x']
                                  )


Żory
Żywiec
Świętochłowice
Będzin
Bielsko-Biała
Bielsko
Bieruń-Lędziny
Bytom
Chorzów
Cieszyn
Częstochowa City
Częstochowa
Dąbrowa Górnicza
Gliwice City
Gliwice
Jastrzębie-Zdrój
Jaworzno
Kłobuck
Katowice City
Lubliniec
Mikołów
Mysłowice
Myszków
Piekary Śląskie
Pszczyna
Racibórz
Ruda Śląska
Rybnik City
Rybnik
Siemianowice Śląskie
Sosnowiec
Tarnowskie
Tychy City
Wodzisław
Zabrze
Zawiercie


In [22]:
print(location_venues.shape)
location_venues

(168, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0                    Żory              50.022560               18.685270   
1                    Żory              50.022560               18.685270   
2                    Żory              50.022560               18.685270   
3                    Żory              50.022560               18.685270   
4                    Żory              50.022560               18.685270   
5                    Żory              50.022560               18.685270   
6                    Żory              50.022560               18.685270   
7                    Żory              50.022560               18.685270   
8                    Żory              50.022560               18.685270   
9                    Żory              50.022560               18.685270   
10                   Żory              50.022560               18.685270   
11                 Żywiec              49.587275               19.184707   
12                 Żywiec              49.587275               19.184707   
13                 Żywiec              49.587275               19.184707   
14                 Żywiec              49.587275               19.184707   
15                 Żywiec              49.587275               19.184707   
16                 Żywiec              49.587275               19.184707   
17                 Żywiec              49.587275               19.184707   
18                 Żywiec              49.587275               19.184707   
19                 Żywiec              49.587275               19.184707   
20                 Żywiec              49.587275               19.184707   
21                 Żywiec              49.587275               19.184707   
22                 Żywiec              49.587275               19.184707   
23                 Żywiec              49.587275               19.184707   
24                 Żywiec              49.587275               19.184707   
25                 Żywiec              49.587275               19.184707   
26                 Żywiec              49.587275               19.184707   
27                 Żywiec              49.587275               19.184707   
28                 Żywiec              49.587275               19.184707   
29                 Żywiec              49.587275               19.184707   
30         Świętochłowice              50.235390               18.826438   
31         Świętochłowice              50.235390               18.826438   
32                 Będzin              50.371653               19.116783   
33                 Będzin              50.371653               19.116783   
34                 Będzin              50.371653               19.116783   
35                 Będzin              50.371653               19.116783   
36                 Będzin              50.371653               19.116783   
37                 Będzin              50.371653               19.116783   
38                 Będzin              50.371653               19.116783   
39          Bielsko-Biała              49.791412               19.058871   
40          Bielsko-Biała              49.791412               19.058871   
41          Bielsko-Biała              49.791412               19.058871   
42          Bielsko-Biała              49.791412               19.058871   
43                Bielsko              49.804282               19.046777   
44                Bielsko              49.804282               19.046777   
45         Bieruń-Lędziny              50.052411               19.153136   
46                  Bytom              50.322524               18.847702   
47                  Bytom              50.322524               18.847702   
48                  Bytom              50.322524               18.847702   
49                  Bytom              50.322524               18.847702   
50                  Bytom              50.322524               18.847702   
51                Chorzów              50.256611             

### Let's find out how many unique categories can be curated from all the returned venues

In [23]:
print('There are {} uniques categories.'.format(len(location_venues['Venue Category'].unique())))

There are 25 uniques categories.


In [24]:
location_venues['Venue Category'].unique()

array(['Lake', 'Mountain', 'Forest', 'Paintball Field', 'Scenic Lookout',
       'River', 'Go Kart Track', 'Golf Course', 'Trail',
       'Other Great Outdoors', 'Ski Chairlift', 'Public Art',
       'Bowling Alley', 'Ski Area', 'National Park', 'Dive Spot',
       'Church', 'Pool', 'Sculpture Garden', 'Hill', 'Shopping Mall',
       'Park', 'Sports Bar', 'Hotel', 'Nature Preserve'], dtype=object)

## Let's check how many venues were returned for each neighborhood

In [25]:
venue_count = location_venues.groupby(['Neighborhood']).size().reset_index(name='venue_count')
venue_count.head

location_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                 
Bielsko                                   2                       2      2   
Bielsko-Biała                             4                       4      4   
Bieruń-Lędziny                            1                       1      1   
Bytom                                     5                       5      5   
Będzin                                    7                       7      7   
Chorzów                                   3                       3      3   
Cieszyn                                   4                       4      4   
Częstochowa                               6                       6      6   
Częstochowa City                          8                       8      8   
Dąbrowa Górnicza                          3                       3      3   
Gliwice                                   1                       1      1   
Gliwice City                              4                       4      4   
Jaworzno                                  5                       5      5   
Katowice City                             6                       6      6   
Kłobuck                                   1                       1      1   
Lubliniec                                 1                       1      1   
Mikołów                                  10                      10     10   
Myszków                                   2                       2      2   
Mysłowice                                 1                       1      1   
Piekary Śląskie                           9                       9      9   
Pszczyna                                  6                       6      6   
Racibórz                                  3                       3      3   
Ruda Śląska                               4                       4      4   
Rybnik                                   11                      11     11   
Rybnik City                               2                       2      2   
Siemianowice Śląskie                      3                       3      3   
Sosnowiec                                 3                       3      3   
Tarnowskie                                3                       3      3   
Tychy City                                4                       4      4   
Wodzisław                                 4                       4      4   
Zabrze                                    4                       4      4   
Zawiercie                                 6                       6      6   
Świętochłowice                            2                       2      2   
Żory                                     11                      11     11   
Żywiec                                   19                      19     19   

                      Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                           
Bielsko                            2                2               2  
Bielsko-Biała                      4                4               4  
Bieruń-Lędziny                     1                1               1  
Bytom                              5                5               5  
Będzin                             7                7               7  
Chorzów                            3                3               3  
Cieszyn                            4                4               4  
Częstochowa                        6                6               6  
Częstochowa City                   8                8               8  
Dąbrowa Górnicza                   3                3               3  
Gliwice                            1                1               1  
Gliwice City                       4                4               4  
Jaworzno                           5                5               5  
Katowice City                      6                6  

## Let's visualise the distribution of venues in the neighborhoods

In [26]:
!wget -q -O 'stanford-xh662zc5620-geojson.json' https://raw.githubusercontent.com/KatH-M/Coursera_Capstone/master/stanford-xh662zc5620-geojson.json
    
Pol_geo = r'stanford-xh662zc5620-geojson.json' # geojson file

# create a plain Katowice map
m = folium.Map(location=[50.18615110527844, 18.9954791009462])


# add a Choropleth map with venue counts determining colour 
folium.Choropleth(
    geo_data=Pol_geo,
    data=venue_count,
    columns=['Neighborhood','venue_count'],
    key_on='feature.properties.name_2',
    #bins=8,
    bins=8,
    fill_color='YlOrRd',
    nan_fill_color='black',
    fill_opacity=0.7, 
    nan_fill_opacity=None,
    line_opacity=0.2,
    legend_name='Count of Venues',
    highlight=True,
    name='Neighborhood'
).add_to(m)

# add an overlay of highlighting and the Area Name when hovering over the polygon
folium.GeoJson(data=Pol_geo,
               name='name_2',
               style_function=lambda x: {'color':'black','fillColor':'transparent','weight':2},
               tooltip=folium.GeoJsonTooltip(fields=['name_2'],
                                            labels=False,
                                            sticky=False),
               highlight_function=lambda x: {'weight':3,'fillColor':'grey'}
).add_to(m)

m


 ### Let's analyze each neighborhood in terms of existing venues for each unique category

In [27]:
# one hot encoding
Silesian_onehot = pd.get_dummies(location_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
Silesian_onehot['Neighborhood'] = location_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [Silesian_onehot.columns[-1]] + list(Silesian_onehot.columns[:-1])
Silesian_onehot = Silesian_onehot[fixed_columns]

#Silesian_onehot.head()
Silesian_onehot.head()

Neighborhood  Bowling Alley  Church  Dive Spot  Forest  Go Kart Track  \
0         Żory              0       0          0       0              0   
1         Żory              0       0          0       0              0   
2         Żory              0       0          0       0              0   
3         Żory              0       0          0       0              0   
4         Żory              0       0          0       0              0   

   Golf Course  Hill  Hotel  Lake  Mountain  National Park  Nature Preserve  \
0            0     0      0     1         0              0                0   
1            0     0      0     1         0              0                0   
2            0     0      0     1         0              0                0   
3            0     0      0     1         0              0                0   
4            0     0      0     0         1              0                0   

   Other Great Outdoors  Paintball Field  Park  Pool  Public Art  River  \
0                     0                0     0     0           0      0   
1                     0                0     0     0           0      0   
2                     0                0     0     0           0      0   
3                     0                0     0     0           0      0   
4                     0                0     0     0           0      0   

   Scenic Lookout  Sculpture Garden  Shopping Mall  Ski Area  Ski Chairlift  \
0               0                 0              0         0              0   
1               0                 0              0         0              0   
2               0                 0              0         0              0   
3               0                 0              0         0              0   
4               0                 0              0         0              0   

   Sports Bar  Trail  
0           0      0  
1           0      0  
2           0      0  
3           0      0  
4           0      0

In [28]:
Silesian_onehot.shape

(168, 26)

### Rows were grouped by neighborhood and the mean of the frequency of occurrence of each category was calulated.


        

In [29]:
Silesian_grouped = Silesian_onehot.groupby('Neighborhood').mean().reset_index()
Silesian_grouped

Neighborhood  Bowling Alley  Church  Dive Spot    Forest  \
0                Bielsko       0.000000    0.00   0.000000  0.000000   
1          Bielsko-Biała       0.000000    0.00   0.000000  0.000000   
2         Bieruń-Lędziny       0.000000    0.00   0.000000  0.000000   
3                  Bytom       0.000000    0.00   0.000000  0.000000   
4                 Będzin       0.000000    0.00   0.000000  0.000000   
5                Chorzów       0.333333    0.00   0.000000  0.000000   
6                Cieszyn       0.000000    0.00   0.000000  0.000000   
7            Częstochowa       0.000000    0.00   0.000000  0.000000   
8       Częstochowa City       0.375000    0.00   0.000000  0.000000   
9       Dąbrowa Górnicza       0.000000    0.00   0.333333  0.000000   
10               Gliwice       0.000000    0.00   0.000000  0.000000   
11          Gliwice City       0.250000    0.25   0.000000  0.000000   
12              Jaworzno       0.200000    0.00   0.200000  0.000000   
13         Katowice City       0.333333    0.00   0.000000  0.000000   
14               Kłobuck       0.000000    0.00   0.000000  0.000000   
15             Lubliniec       0.000000    0.00   0.000000  0.000000   
16               Mikołów       0.100000    0.00   0.000000  0.000000   
17               Myszków       0.500000    0.00   0.000000  0.000000   
18             Mysłowice       0.000000    0.00   0.000000  0.000000   
19       Piekary Śląskie       0.111111    0.00   0.000000  0.000000   
20              Pszczyna       0.000000    0.00   0.000000  0.166667   
21              Racibórz       0.000000    0.00   0.000000  0.333333   
22           Ruda Śląska       0.250000    0.00   0.000000  0.000000   
23                Rybnik       0.000000    0.00   0.000000  0.181818   
24           Rybnik City       0.000000    0.00   0.000000  0.500000   
25  Siemianowice Śląskie       0.333333    0.00   0.000000  0.000000   
26             Sosnowiec       0.000000    0.00   0.333333  0.000000   
27            Tarnowskie       0.000000    0.00   0.000000  0.000000   
28            Tychy City       0.250000    0.00   0.000000  0.000000   
29             Wodzisław       0.000000    0.00   0.000000  0.000000   
30                Zabrze       0.250000    0.25   0.000000  0.000000   
31             Zawiercie       0.000000    0.00   0.000000  0.166667   
32        Świętochłowice       0.000000    0.00   0.000000  0.000000   
33                  Żory       0.000000    0.00   0.000000  0.090909   
34                Żywiec       0.000000    0.00   0.000000  0.000000   

    Go Kart Track  Golf Course  Hill  Hotel      Lake  Mountain  \
0        0.000000     0.000000   0.0   0.00  0.000000  1.000000   
1        0.000000     0.000000   0.0   0.00  0.250000  0.500000   
2        0.000000     0.000000   0.0   0.00  1.000000  0.000000   
3        0.000000     0.000000   0.0   0.00  0.200000  0.200000   
4        0.142857     0.142857   0.0   0.00  0.714286  0.000000   
5        0.000000     0.000000   0.0   0.00  0.000000  0.333333   
6        0.000000     0.000000   0.0   0.00  0.000000  0.500000   
7        0.000000     0.000000   0.0   0.00  0.333333  0.333333   
8        0.125000     0.125000   0.0   0.00  0.125000  0.000000   
9        0.000000     0.000000   0.0   0.00  0.666667  0.000000   
10       0.000000     0.000000   0.0   0.00  1.000000  0.000000   
11       0.000000     0.000000   0.0   0.00  0.000000  0.250000   
12       0.000000     0.000000   0.0   0.00  0.200000  0.000000   
13       0.000000     0.000000   0.0   0.00  0.333333  0.000000   
14       0.000000     0.000000   0.0   0.00  1.000000  0.000000   
15       0.000000     0.000000   0.0   0.00  1.000000  0.000000   
16       0.000000     0.000000   0.2   0.00  0.600000  0.000000   
17       0.000000     0.000000   0.0   0.00  0.000000  0.000000   
18       0.000000     0.000000   0.0   0.00  0.000000  0.000000   
19       0.000000     0.111111   0.0   0.00  0.333333  0.000000   
20       0.0

### Let's confirm the new size of the dataframe

In [30]:
Silesian_grouped.shape

(35, 26)

### Let's present each neighborhood along with the top 10 most common venues with their mean of the frequency of occurrence for each category

In [32]:
num_top_venues = 10

for hood in Silesian_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = Silesian_grouped[Silesian_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Bielsko----
              venue  freq
0          Mountain   1.0
1     Bowling Alley   0.0
2   Paintball Field   0.0
3        Sports Bar   0.0
4     Ski Chairlift   0.0
5          Ski Area   0.0
6     Shopping Mall   0.0
7  Sculpture Garden   0.0
8    Scenic Lookout   0.0
9             River   0.0


----Bielsko-Biała----
              venue  freq
0          Mountain  0.50
1             Trail  0.25
2              Lake  0.25
3              Park  0.00
4        Sports Bar  0.00
5     Ski Chairlift  0.00
6          Ski Area  0.00
7     Shopping Mall  0.00
8  Sculpture Garden  0.00
9    Scenic Lookout  0.00


----Bieruń-Lędziny----
              venue  freq
0              Lake   1.0
1     Bowling Alley   0.0
2   Paintball Field   0.0
3        Sports Bar   0.0
4     Ski Chairlift   0.0
5          Ski Area   0.0
6     Shopping Mall   0.0
7  Sculpture Garden   0.0
8    Scenic Lookout   0.0
9             River   0.0


----Bytom----
                  venue  freq
0  Other Great Outdoors   0.2
1


### Now let's show it as a dataframe and display the top 10 venues for each neighborhood.

In [33]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [34]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = Silesian_grouped['Neighborhood']

for ind in np.arange(Silesian_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(Silesian_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0         Bielsko              Mountain                 Trail   
1   Bielsko-Biała              Mountain                 Trail   
2  Bieruń-Lędziny                  Lake                 Trail   
3           Bytom  Other Great Outdoors         Ski Chairlift   
4          Będzin                  Lake         Go Kart Track   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0       Nature Preserve                Church             Dive Spot   
1                  Lake       Nature Preserve                Church   
2       Nature Preserve                Church             Dive Spot   
3        Scenic Lookout                  Lake              Mountain   
4           Golf Course                 Trail       Nature Preserve   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                Forest         Go Kart Track           Golf Course   
1             Dive Spot                Forest         Go Kart Track   
2                Forest         Go Kart Track           Golf Course   
3         National Park                Church             Dive Spot   
4                Church             Dive Spot                Forest   

  9th Most Common Venue 10th Most Common Venue  
0                  Hill                  Hotel  
1           Golf Course                   Hill  
2                  Hill                  Hotel  
3                Forest          Go Kart Track  
4                  Hill                  Hotel

In [35]:
neighborhoods_venues_sorted

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0                Bielsko              Mountain                 Trail   
1          Bielsko-Biała              Mountain                 Trail   
2         Bieruń-Lędziny                  Lake                 Trail   
3                  Bytom  Other Great Outdoors         Ski Chairlift   
4                 Będzin                  Lake         Go Kart Track   
5                Chorzów         Bowling Alley            Public Art   
6                Cieszyn              Mountain                 Trail   
7            Częstochowa                  Lake              Mountain   
8       Częstochowa City         Bowling Alley        Scenic Lookout   
9       Dąbrowa Górnicza                  Lake             Dive Spot   
10               Gliwice                  Lake                 Trail   
11          Gliwice City         Bowling Alley                Church   
12              Jaworzno         Bowling Alley             Dive Spot   
13         Katowice City         Bowling Alley                  Lake   
14               Kłobuck                  Lake                 Trail   
15             Lubliniec                  Lake                 Trail   
16               Mikołów                  Lake                  Hill   
17               Myszków         Bowling Alley        Scenic Lookout   
18             Mysłowice        Scenic Lookout                 Trail   
19       Piekary Śląskie                  Lake  Other Great Outdoors   
20              Pszczyna                  Lake                Forest   
21              Racibórz                Forest        Scenic Lookout   
22           Ruda Śląska                  Hill         Bowling Alley   
23                Rybnik                Forest        Scenic Lookout   
24           Rybnik City         Shopping Mall                Forest   
25  Siemianowice Śląskie         Bowling Alley      Sculpture Garden   
26             Sosnowiec             Dive Spot         Go Kart Track   
27            Tarnowskie  Other Great Outdoors         Ski Chairlift   
28            Tychy City                  Lake  Other Great Outdoors   
29             Wodzisław           Golf Course                 Hotel   
30                Zabrze         Bowling Alley                Church   
31             Zawiercie                  Lake              Mountain   
32        Świętochłowice                  Lake              Mountain   
33                  Żory                  Lake                Forest   
34                Żywiec              Mountain                 River   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0        Nature Preserve                Church             Dive Spot   
1                   Lake       Nature Preserve                Church   
2        Nature Preserve                Church             Dive Spot   
3         Scenic Lookout                  Lake              Mountain   
4            Golf Course                 Trail       Nature Preserve   
5               Mountain       Nature Preserve                Church   
6               Ski Area       Nature Preserve                Church   
7                  River         National Park                 Trail   
8          Go Kart Track           Golf Course                  Lake   
9                  Trail       Nature Preserve                Church   
10       Nature Preserve                Church             Dive Spot   
11        Scenic Lookout              Mountain       Nature Preserve   
12        Scenic Lookout                  Pool                  Lake   
13      Sculpture Garden        Scenic Lookout         National Park   
14       Nature Preserve                Church             Dive Spot   
15       Nature Preserve                Church             Dive Spot   
16         Bowling Alley      Sculpture Garden       Nature Preserve   
17       Nature Preserve                Church             Dive Spot   
18       Nature Preserve                Church     

## Clustering. Run k-means algorythm to cluster the neighborhoods into 5 clusters based on the common venues


In [36]:
# set number of clusters
kclusters = 5

Silesian_grouped_clustering = Silesian_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(Silesian_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([3, 3, 2, 4, 2, 0, 3, 4, 0, 2], dtype=int32)

In [37]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

Silesian_merged = Silesian_neigh

# merge Silesian_grouped with Silesian_neigh to add latitude/longitude for each neighborhood
Silesian_merged = Silesian_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

Silesian_merged.head() # check the last columns!

region    Neighborhood  centroid_x  centroid_y  \
0  Silesian            Żory   18.685270   50.022560   
1  Silesian          Żywiec   19.184707   49.587275   
2  Silesian  Świętochłowice   18.826438   50.235390   
3  Silesian          Będzin   19.116783   50.371653   
4  Silesian   Bielsko-Biała   19.058871   49.791412   

                                         coordinates  Cluster Labels  \
0  {'type': 'MultiPolygon', 'coordinates': [[[[18...             2.0   
1  {'type': 'MultiPolygon', 'coordinates': [[[[19...             3.0   
2  {'type': 'MultiPolygon', 'coordinates': [[[[18...             4.0   
3  {'type': 'MultiPolygon', 'coordinates': [[[[19...             2.0   
4  {'type': 'MultiPolygon', 'coordinates': [[[[19...             3.0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0                  Lake                Forest              Mountain   
1              Mountain                 River        Scenic Lookout   
2                  Lake              Mountain                 Trail   
3                  Lake         Go Kart Track           Golf Course   
4              Mountain                 Trail                  Lake   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0       Paintball Field                 Trail       Nature Preserve   
1                 Trail         National Park                Church   
2       Nature Preserve                Church             Dive Spot   
3                 Trail       Nature Preserve                Church   
4       Nature Preserve                Church             Dive Spot   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0                Church             Dive Spot         Go Kart Track   
1             Dive Spot                Forest         Go Kart Track   
2                Forest         Go Kart Track           Golf Course   
3             Dive Spot                Forest                  Hill   
4                Forest         Go Kart Track           Golf Course   

  10th Most Common Venue  
0            Golf Course  
1            Golf Course  
2                   Hill  
3                  Hotel  
4                   Hill

In [38]:
Silesian_merged

region          Neighborhood  centroid_x  centroid_y  \
0   Silesian                  Żory   18.685270   50.022560   
1   Silesian                Żywiec   19.184707   49.587275   
2   Silesian        Świętochłowice   18.826438   50.235390   
3   Silesian                Będzin   19.116783   50.371653   
4   Silesian         Bielsko-Biała   19.058871   49.791412   
5   Silesian               Bielsko   19.046777   49.804282   
6   Silesian        Bieruń-Lędziny   19.153136   50.052411   
7   Silesian                 Bytom   18.847702   50.322524   
8   Silesian               Chorzów   18.877021   50.256611   
9   Silesian               Cieszyn   18.811055   49.731717   
10  Silesian      Częstochowa City   19.108907   50.765166   
11  Silesian           Częstochowa   19.362686   50.761963   
12  Silesian      Dąbrowa Górnicza   19.278621   50.305332   
13  Silesian          Gliwice City   18.617840   50.273288   
14  Silesian               Gliwice   18.501074   50.333499   
15  Silesian      Jastrzębie-Zdrój   18.614513   49.950146   
16  Silesian              Jaworzno   19.283292   50.175453   
17  Silesian               Kłobuck   18.842704   50.883408   
18  Silesian         Katowice City   18.995479   50.186151   
19  Silesian             Lubliniec   18.753959   50.629159   
20  Silesian               Mikołów   18.821696   50.109081   
21  Silesian             Mysłowice   19.147434   50.152310   
22  Silesian               Myszków   19.302124   50.565072   
23  Silesian       Piekary Śląskie   18.918126   50.335267   
24  Silesian              Pszczyna   18.888372   49.965744   
25  Silesian              Racibórz   18.219360   50.100139   
26  Silesian           Ruda Śląska   18.763319   50.207801   
27  Silesian           Rybnik City   18.516108   50.089914   
28  Silesian                Rybnik   18.534643   50.099888   
29  Silesian  Siemianowice Śląskie   18.960857   50.278223   
30  Silesian             Sosnowiec   19.184173   50.245526   
31  Silesian            Tarnowskie   18.799812   50.445403   
32  Silesian            Tychy City   19.009399   50.085994   
33  Silesian             Wodzisław   18.401856   49.985707   
34  Silesian                Zabrze   18.744917   50.275122   
35  Silesian             Zawiercie   19.618607   50.474186   

                                          coordinates  Cluster Labels  \
0   {'type': 'MultiPolygon', 'coordinates': [[[[18...             2.0   
1   {'type': 'MultiPolygon', 'coordinates': [[[[19...             3.0   
2   {'type': 'MultiPolygon', 'coordinates': [[[[18...             4.0   
3   {'type': 'MultiPolygon', 'coordinates': [[[[19...             2.0   
4   {'type': 'MultiPolygon', 'coordinates': [[[[19...             3.0   
5   {'type': 'MultiPolygon', 'coordinates': [[[[19...             3.0   
6   {'type': 'MultiPolygon', 'coordinates': [[[[19...             2.0   
7   {'type': 'MultiPolygon', 'coordinates': [[[[18...             4.0   
8   {'type': 'MultiPolygon', 'coordinates': [[[[18...             0.0   
9   {'type': 'MultiPolygon', 'coordinates': [[[[18...             3.0   
10  {'type': 'MultiPolygon', 'coordinates': [[[[19...             0.0   
11  {'type': 'MultiPolygon', 'coordinates': [[[[19...             4.0   
12  {'type': 'MultiPolygon', 'coordinates': [[[[19...             2.0   
13  {'type': 'MultiPolygon', 'coordinates': [[[[18...             0.0   
14  {'type': 'MultiPolygon', 'coordinates': [[[[18...             2.0   
15  {'type': 'MultiPolygon', 'coordinates': [[[[18...             NaN   
16  {'type': 'MultiPolygon', 'coordinates': [[[[19...             0.0   
17  {'type': 'MultiPolygon', 'coordinates': [[[[19...             2.0   
18  {'type': 'MultiPolygon', 'coordinates': [[[[18...             0.0   
19  {'type': 'MultiPolygon', 'coordinates': [[[[19...             2.0   
20  {'type': 'MultiPolygon', 'coordinates': [[[[18...             2.0   
21  {'type': 'MultiPolygon', 'coordinates': [[[[19...             1.0   
22  {'type': 'MultiPolygon', 'co

### I had to remove Jastrzebie Zdroj as it does not contain any venues

In [39]:
Silesian_merged = Silesian_merged[Silesian_merged['Cluster Labels'].notna()]
Silesian_merged

region          Neighborhood  centroid_x  centroid_y  \
0   Silesian                  Żory   18.685270   50.022560   
1   Silesian                Żywiec   19.184707   49.587275   
2   Silesian        Świętochłowice   18.826438   50.235390   
3   Silesian                Będzin   19.116783   50.371653   
4   Silesian         Bielsko-Biała   19.058871   49.791412   
5   Silesian               Bielsko   19.046777   49.804282   
6   Silesian        Bieruń-Lędziny   19.153136   50.052411   
7   Silesian                 Bytom   18.847702   50.322524   
8   Silesian               Chorzów   18.877021   50.256611   
9   Silesian               Cieszyn   18.811055   49.731717   
10  Silesian      Częstochowa City   19.108907   50.765166   
11  Silesian           Częstochowa   19.362686   50.761963   
12  Silesian      Dąbrowa Górnicza   19.278621   50.305332   
13  Silesian          Gliwice City   18.617840   50.273288   
14  Silesian               Gliwice   18.501074   50.333499   
16  Silesian              Jaworzno   19.283292   50.175453   
17  Silesian               Kłobuck   18.842704   50.883408   
18  Silesian         Katowice City   18.995479   50.186151   
19  Silesian             Lubliniec   18.753959   50.629159   
20  Silesian               Mikołów   18.821696   50.109081   
21  Silesian             Mysłowice   19.147434   50.152310   
22  Silesian               Myszków   19.302124   50.565072   
23  Silesian       Piekary Śląskie   18.918126   50.335267   
24  Silesian              Pszczyna   18.888372   49.965744   
25  Silesian              Racibórz   18.219360   50.100139   
26  Silesian           Ruda Śląska   18.763319   50.207801   
27  Silesian           Rybnik City   18.516108   50.089914   
28  Silesian                Rybnik   18.534643   50.099888   
29  Silesian  Siemianowice Śląskie   18.960857   50.278223   
30  Silesian             Sosnowiec   19.184173   50.245526   
31  Silesian            Tarnowskie   18.799812   50.445403   
32  Silesian            Tychy City   19.009399   50.085994   
33  Silesian             Wodzisław   18.401856   49.985707   
34  Silesian                Zabrze   18.744917   50.275122   
35  Silesian             Zawiercie   19.618607   50.474186   

                                          coordinates  Cluster Labels  \
0   {'type': 'MultiPolygon', 'coordinates': [[[[18...             2.0   
1   {'type': 'MultiPolygon', 'coordinates': [[[[19...             3.0   
2   {'type': 'MultiPolygon', 'coordinates': [[[[18...             4.0   
3   {'type': 'MultiPolygon', 'coordinates': [[[[19...             2.0   
4   {'type': 'MultiPolygon', 'coordinates': [[[[19...             3.0   
5   {'type': 'MultiPolygon', 'coordinates': [[[[19...             3.0   
6   {'type': 'MultiPolygon', 'coordinates': [[[[19...             2.0   
7   {'type': 'MultiPolygon', 'coordinates': [[[[18...             4.0   
8   {'type': 'MultiPolygon', 'coordinates': [[[[18...             0.0   
9   {'type': 'MultiPolygon', 'coordinates': [[[[18...             3.0   
10  {'type': 'MultiPolygon', 'coordinates': [[[[19...             0.0   
11  {'type': 'MultiPolygon', 'coordinates': [[[[19...             4.0   
12  {'type': 'MultiPolygon', 'coordinates': [[[[19...             2.0   
13  {'type': 'MultiPolygon', 'coordinates': [[[[18...             0.0   
14  {'type': 'MultiPolygon', 'coordinates': [[[[18...             2.0   
16  {'type': 'MultiPolygon', 'coordinates': [[[[19...             0.0   
17  {'type': 'MultiPolygon', 'coordinates': [[[[19...             2.0   
18  {'type': 'MultiPolygon', 'coordinates': [[[[18...             0.0   
19  {'type': 'MultiPolygon', 'coordinates': [[[[19...             2.0   
20  {'type': 'MultiPolygon', 'coordinates': [[[[18...             2.0   
21  {'type': 'MultiPolygon', 'coordinates': [[[[19...             1.0   
22  {'type': 'MultiPolygon', 'coordinates': [[[[19...             0.0   
23  {'type': 'MultiPolygon', 'coordinates': [[[[18...             4.0   
24  {'type': 'MultiPo

### I need to change float in Cluster Labels to int as folium map does not like floats

In [40]:
Silesian_merged['Cluster Labels'] = Silesian_merged['Cluster Labels'].astype(int)


/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if __name__ == '__main__':


## Let's show a new dataframe that includes the cluster number as well as the top 10 venues for each neighborhood.

In [41]:
Silesian_merged.head()

region    Neighborhood  centroid_x  centroid_y  \
0  Silesian            Żory   18.685270   50.022560   
1  Silesian          Żywiec   19.184707   49.587275   
2  Silesian  Świętochłowice   18.826438   50.235390   
3  Silesian          Będzin   19.116783   50.371653   
4  Silesian   Bielsko-Biała   19.058871   49.791412   

                                         coordinates  Cluster Labels  \
0  {'type': 'MultiPolygon', 'coordinates': [[[[18...               2   
1  {'type': 'MultiPolygon', 'coordinates': [[[[19...               3   
2  {'type': 'MultiPolygon', 'coordinates': [[[[18...               4   
3  {'type': 'MultiPolygon', 'coordinates': [[[[19...               2   
4  {'type': 'MultiPolygon', 'coordinates': [[[[19...               3   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0                  Lake                Forest              Mountain   
1              Mountain                 River        Scenic Lookout   
2                  Lake              Mountain                 Trail   
3                  Lake         Go Kart Track           Golf Course   
4              Mountain                 Trail                  Lake   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0       Paintball Field                 Trail       Nature Preserve   
1                 Trail         National Park                Church   
2       Nature Preserve                Church             Dive Spot   
3                 Trail       Nature Preserve                Church   
4       Nature Preserve                Church             Dive Spot   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0                Church             Dive Spot         Go Kart Track   
1             Dive Spot                Forest         Go Kart Track   
2                Forest         Go Kart Track           Golf Course   
3             Dive Spot                Forest                  Hill   
4                Forest         Go Kart Track           Golf Course   

  10th Most Common Venue  
0            Golf Course  
1            Golf Course  
2                   Hill  
3                  Hotel  
4                   Hill

In [42]:
Silesian_merged

region          Neighborhood  centroid_x  centroid_y  \
0   Silesian                  Żory   18.685270   50.022560   
1   Silesian                Żywiec   19.184707   49.587275   
2   Silesian        Świętochłowice   18.826438   50.235390   
3   Silesian                Będzin   19.116783   50.371653   
4   Silesian         Bielsko-Biała   19.058871   49.791412   
5   Silesian               Bielsko   19.046777   49.804282   
6   Silesian        Bieruń-Lędziny   19.153136   50.052411   
7   Silesian                 Bytom   18.847702   50.322524   
8   Silesian               Chorzów   18.877021   50.256611   
9   Silesian               Cieszyn   18.811055   49.731717   
10  Silesian      Częstochowa City   19.108907   50.765166   
11  Silesian           Częstochowa   19.362686   50.761963   
12  Silesian      Dąbrowa Górnicza   19.278621   50.305332   
13  Silesian          Gliwice City   18.617840   50.273288   
14  Silesian               Gliwice   18.501074   50.333499   
16  Silesian              Jaworzno   19.283292   50.175453   
17  Silesian               Kłobuck   18.842704   50.883408   
18  Silesian         Katowice City   18.995479   50.186151   
19  Silesian             Lubliniec   18.753959   50.629159   
20  Silesian               Mikołów   18.821696   50.109081   
21  Silesian             Mysłowice   19.147434   50.152310   
22  Silesian               Myszków   19.302124   50.565072   
23  Silesian       Piekary Śląskie   18.918126   50.335267   
24  Silesian              Pszczyna   18.888372   49.965744   
25  Silesian              Racibórz   18.219360   50.100139   
26  Silesian           Ruda Śląska   18.763319   50.207801   
27  Silesian           Rybnik City   18.516108   50.089914   
28  Silesian                Rybnik   18.534643   50.099888   
29  Silesian  Siemianowice Śląskie   18.960857   50.278223   
30  Silesian             Sosnowiec   19.184173   50.245526   
31  Silesian            Tarnowskie   18.799812   50.445403   
32  Silesian            Tychy City   19.009399   50.085994   
33  Silesian             Wodzisław   18.401856   49.985707   
34  Silesian                Zabrze   18.744917   50.275122   
35  Silesian             Zawiercie   19.618607   50.474186   

                                          coordinates  Cluster Labels  \
0   {'type': 'MultiPolygon', 'coordinates': [[[[18...               2   
1   {'type': 'MultiPolygon', 'coordinates': [[[[19...               3   
2   {'type': 'MultiPolygon', 'coordinates': [[[[18...               4   
3   {'type': 'MultiPolygon', 'coordinates': [[[[19...               2   
4   {'type': 'MultiPolygon', 'coordinates': [[[[19...               3   
5   {'type': 'MultiPolygon', 'coordinates': [[[[19...               3   
6   {'type': 'MultiPolygon', 'coordinates': [[[[19...               2   
7   {'type': 'MultiPolygon', 'coordinates': [[[[18...               4   
8   {'type': 'MultiPolygon', 'coordinates': [[[[18...               0   
9   {'type': 'MultiPolygon', 'coordinates': [[[[18...               3   
10  {'type': 'MultiPolygon', 'coordinates': [[[[19...               0   
11  {'type': 'MultiPolygon', 'coordinates': [[[[19...               4   
12  {'type': 'MultiPolygon', 'coordinates': [[[[19...               2   
13  {'type': 'MultiPolygon', 'coordinates': [[[[18...               0   
14  {'type': 'MultiPolygon', 'coordinates': [[[[18...               2   
16  {'type': 'MultiPolygon', 'coordinates': [[[[19...               0   
17  {'type': 'MultiPolygon', 'coordinates': [[[[19...               2   
18  {'type': 'MultiPolygon', 'coordinates': [[[[18...               0   
19  {'type': 'MultiPolygon', 'coordinates': [[[[19...               2   
20  {'type': 'MultiPolygon', 'coordinates': [[[[18...               2   
21  {'type': 'MultiPolygon', 'coordinates': [[[[19...               1   
22  {'type': 'MultiPolygon', 'coordinates': [[[[19...               0   
23  {'type': 'MultiPolygon', 'coordinates': [[[[18...               4   
24  {'type': 'MultiPo

## Let's examine clusters and determine the discriminating venue categories that distinguish each cluster.

### Cluster 1 (green) - cluster of locations with highly recommended locations surrounding: various, not consistent, entertainment venues: bowling 

In [43]:
Silesian_merged.loc[Silesian_merged['Cluster Labels'] == 0, Silesian_merged.columns[[1] + list(range(5, Silesian_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
8                Chorzów               0         Bowling Alley   
10      Częstochowa City               0         Bowling Alley   
13          Gliwice City               0         Bowling Alley   
16              Jaworzno               0         Bowling Alley   
18         Katowice City               0         Bowling Alley   
22               Myszków               0         Bowling Alley   
25              Racibórz               0                Forest   
26           Ruda Śląska               0                  Hill   
29  Siemianowice Śląskie               0         Bowling Alley   
30             Sosnowiec               0             Dive Spot   
34                Zabrze               0         Bowling Alley   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
8             Public Art              Mountain       Nature Preserve   
10        Scenic Lookout         Go Kart Track           Golf Course   
13                Church        Scenic Lookout              Mountain   
16             Dive Spot        Scenic Lookout                  Pool   
18                  Lake      Sculpture Garden        Scenic Lookout   
22        Scenic Lookout       Nature Preserve                Church   
25        Scenic Lookout                 River                 Trail   
26         Bowling Alley              Mountain       Nature Preserve   
29      Sculpture Garden            Public Art         National Park   
30         Go Kart Track        Scenic Lookout                 Trail   
34                Church        Scenic Lookout              Mountain   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
8                 Church             Dive Spot                Forest   
10                  Lake       Nature Preserve                Church   
13       Nature Preserve             Dive Spot                Forest   
16                  Lake         National Park                Church   
18         National Park                Church             Dive Spot   
22             Dive Spot                Forest         Go Kart Track   
25         National Park                Church             Dive Spot   
26                Church             Dive Spot                Forest   
29                Church             Dive Spot                Forest   
30       Nature Preserve                Church                Forest   
34       Nature Preserve             Dive Spot                Forest   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
8          Go Kart Track           Golf Course                   Hill  
10             Dive Spot                Forest                   Hill  
13         Go Kart Track           Golf Course                   Hill  
16                Forest         Go Kart Track            Golf Course  
18                Forest         Go Kart Track            Golf Course  
22           Golf Course                  Hill                  Hotel  
25         Go Kart Track           Golf Course                   Hill  
26         Go Kart Track           Golf Course                  Hotel  
29         Go Kart Track           Golf Course                   Hill  
30           Golf Course                  Hill                  Hotel  
34         Go Kart Track           Golf Course                   Hill

### Cluster 2 (orange) - cluster of locations with highly recommended locations surrounding: scenic lookout, trail, entertainment: go card and golf course

In [44]:
Silesian_merged.loc[Silesian_merged['Cluster Labels'] == 1, Silesian_merged.columns[[1] + list(range(5, Silesian_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
21    Mysłowice               1        Scenic Lookout                 Trail   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
21       Nature Preserve                Church             Dive Spot   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
21                Forest         Go Kart Track           Golf Course   

   9th Most Common Venue 10th Most Common Venue  
21                  Hill                  Hotel

### Cluster 3 (red) - cluster of locations with highly recommended locations surrounding: lake and natural preserve,  entertainment: go kart, paintball

In [45]:
Silesian_merged.loc[Silesian_merged['Cluster Labels'] == 2, Silesian_merged.columns[[1] + list(range(5, Silesian_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
0               Żory               2                  Lake   
3             Będzin               2                  Lake   
6     Bieruń-Lędziny               2                  Lake   
12  Dąbrowa Górnicza               2                  Lake   
14           Gliwice               2                  Lake   
17           Kłobuck               2                  Lake   
19         Lubliniec               2                  Lake   
20           Mikołów               2                  Lake   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0                 Forest              Mountain       Paintball Field   
3          Go Kart Track           Golf Course                 Trail   
6                  Trail       Nature Preserve                Church   
12             Dive Spot                 Trail       Nature Preserve   
14                 Trail       Nature Preserve                Church   
17                 Trail       Nature Preserve                Church   
19                 Trail       Nature Preserve                Church   
20                  Hill         Bowling Alley      Sculpture Garden   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0                  Trail       Nature Preserve                Church   
3        Nature Preserve                Church             Dive Spot   
6              Dive Spot                Forest         Go Kart Track   
12                Church                Forest         Go Kart Track   
14             Dive Spot                Forest         Go Kart Track   
17             Dive Spot                Forest         Go Kart Track   
19             Dive Spot                Forest         Go Kart Track   
20       Nature Preserve                Church             Dive Spot   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0              Dive Spot         Go Kart Track            Golf Course  
3                 Forest                  Hill                  Hotel  
6            Golf Course                  Hill                  Hotel  
12           Golf Course                  Hill                  Hotel  
14           Golf Course                  Hill                  Hotel  
17           Golf Course                  Hill                  Hotel  
19           Golf Course                  Hill                  Hotel  
20                Forest         Go Kart Track            Golf Course

### Cluster 4 (purple) - cluster of locations with highly recommended locations surrounding:mountains and  trail, entertainment: diving, go kart, golf course

In [46]:
Silesian_merged.loc[Silesian_merged['Cluster Labels'] == 3, Silesian_merged.columns[[1] + list(range(5, Silesian_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
1         Żywiec               3              Mountain                 River   
4  Bielsko-Biała               3              Mountain                 Trail   
5        Bielsko               3              Mountain                 Trail   
9        Cieszyn               3              Mountain                 Trail   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
1        Scenic Lookout                 Trail         National Park   
4                  Lake       Nature Preserve                Church   
5       Nature Preserve                Church             Dive Spot   
9              Ski Area       Nature Preserve                Church   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
1                Church             Dive Spot                Forest   
4             Dive Spot                Forest         Go Kart Track   
5                Forest         Go Kart Track           Golf Course   
9             Dive Spot                Forest         Go Kart Track   

  9th Most Common Venue 10th Most Common Venue  
1         Go Kart Track            Golf Course  
4           Golf Course                   Hill  
5                  Hill                  Hotel  
9           Golf Course                   Hill

### Cluster 5 (blue) -  cluster of locations with highly recommended locations surrounding: lake, forest, entertainment: bowling, diving

In [47]:
Silesian_merged.loc[Silesian_merged['Cluster Labels'] == 4, Silesian_merged.columns[[1] + list(range(5, Silesian_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
2    Świętochłowice               4                  Lake   
7             Bytom               4  Other Great Outdoors   
11      Częstochowa               4                  Lake   
23  Piekary Śląskie               4                  Lake   
24         Pszczyna               4                  Lake   
27      Rybnik City               4         Shopping Mall   
28           Rybnik               4                Forest   
31       Tarnowskie               4  Other Great Outdoors   
32       Tychy City               4                  Lake   
33        Wodzisław               4           Golf Course   
35        Zawiercie               4                  Lake   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
2               Mountain                 Trail       Nature Preserve   
7          Ski Chairlift        Scenic Lookout                  Lake   
11              Mountain                 River         National Park   
23  Other Great Outdoors        Scenic Lookout           Golf Course   
24                Forest        Scenic Lookout           Golf Course   
27                Forest                 Trail       Nature Preserve   
28        Scenic Lookout                  Lake              Mountain   
31         Ski Chairlift                  Lake       Nature Preserve   
32  Other Great Outdoors         Bowling Alley              Ski Area   
33                 Hotel                  Lake            Sports Bar   
35              Mountain       Nature Preserve                Forest   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
2                 Church             Dive Spot                Forest   
7               Mountain         National Park                Church   
11                 Trail       Nature Preserve                Church   
23            Public Art         Bowling Alley         Ski Chairlift   
24                 Trail       Nature Preserve                Church   
27                Church             Dive Spot         Go Kart Track   
28         Shopping Mall         Go Kart Track                  Park   
31                Church             Dive Spot                Forest   
32         Shopping Mall                Church             Dive Spot   
33                 Trail       Nature Preserve                Church   
35                 Trail                Church             Dive Spot   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
2          Go Kart Track           Golf Course                   Hill  
7              Dive Spot                Forest          Go Kart Track  
11             Dive Spot                Forest          Go Kart Track  
23      Sculpture Garden              Ski Area                 Church  
24             Dive Spot         Go Kart Track                   Hill  
27           Golf Course                  Hill                  Hotel  
28                 Trail         National Park                 Church  
31         Go Kart Track           Golf Course                   Hill  
32                Forest         Go Kart Track            Golf Course  
33             Dive Spot                Forest          Go Kart Track  
35         Go Kart Track           Golf Course                   Hill

## Finally, let's visualize the resulting clusters

In [48]:
# create map of Katowice using lat and lng of Katowice
map_clusters = folium.Map(location=[latitude,longitude], zoom_start=12)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(Silesian_merged['centroid_y'], Silesian_merged['centroid_x'], Silesian_merged['Neighborhood'], Silesian_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-3],
        fill=True,
        fill_color=rainbow[cluster-3],
        fill_opacity=0.9).add_to(map_clusters)
        
map_clusters

### Let's Investigate Żywiec sourounding further as it shows good combination of recommended entertainment and location. In this search categores belong to hotel/ conference facilities

In [49]:
categories='4bf58dd8d48988d12f951735,4bf58dd8d48988d1ff931735,52e81612bcbc57f1066b7a26,4bf58dd8d48988d1fa931735'   

#near = 'Żywiec, Poland' 
LIMIT=100
radius = 20000
#The geograpical coordinate of Żywiec are 49.6890338, 19.20305.
lat =49.6890338
lng =19.20305

    # create the API request URL
url = 'https://api.foursquare.com/v2/venues/explore?&categoryId={}\
&client_id={}&client_secret={}&ll={},{}&v={}\
&limit={}&radius={}'.format(
        categories,
        CLIENT_ID, 
        CLIENT_SECRET, 
        lat,
        lng,
        VERSION,
        LIMIT,
        radius)

    # make the GET request
results = requests.get(url).json()
#total = int(results['response']['totalResults'])
#results = results['response']['groups'][0]['items']
url
results
        
    
    # return only relevant information for each nearby venue
  #  venue_list.append([(
   #     v['venue']['name'], 
    #    v['venue']['categories'][0]['name'],
     #   v['venue']['location']['lat'], 
      #  v['venue']['location']['lng']) for v in results])
    
    #return venue_list
   

{'meta': {'code': 200, 'requestId': '5f3b1f4fcf2d854abd3d62f9'},
 'response': {'headerLocation': 'Żywiec',
  'headerFullLocation': 'Żywiec',
  'headerLocationGranularity': 'city',
  'query': 'resort',
  'totalResults': 24,
  'suggestedBounds': {'ne': {'lat': 49.869033980000175,
    'lng': 19.480765525796343},
   'sw': {'lat': 49.50903361999982, 'lng': 18.92533447420366}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '51bc4624498ef4bedaf74028',
       'name': 'Hotel & Spa Kocierz',
       'location': {'address': 'ul. Beskidzka 206',
        'lat': 49.77846716198133,
        'lng': 19.31696445616376,
        'labeledLatLngs': [{'label': 'display',
          'lat': 49.77846716198133,
          'lng': 19.31696445616376}],
        'distance': 12895,
        'cc': 'PL',
    

In [50]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [51]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng', 'venue.id']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues

name categories        lat        lng  \
0                Hotel & Spa Kocierz      Hotel  49.778467  19.316964   
1                         Hotel Meta     Resort  49.707065  19.013842   
2                        Qubus Hotel      Hotel  49.826326  19.048905   
3      Hotel President Bielsko-Biala      Hotel  49.823796  19.045053   
4    Papuga Park Hotel Bielsko-Biala     Resort  49.797371  18.985330   
5                    Hotel Dębina***      Hotel  49.673801  19.222909   
6                       Hotel Zimnik      Hotel  49.667134  19.077569   
7                        Czarny Groń     Resort  49.794406  19.387611   
8                        COS Szczyrk      Hotel  49.718090  19.039000   
9                           Panorama      Hotel  49.719816  19.030992   
10               Kocierz Lodge & Spa     Resort  49.778311  19.316909   
11                       Hotel Alpin      Hotel  49.716641  19.028587   
12  Apartamenty Parkowe Resort & SPA      Hotel  49.714056  19.022682   
13        Apartamenty Górska Legenda      Hotel  49.720801  19.008998   
14                       Na Bloniach      Hotel  49.780770  19.053410   
15                    Klimczok Hotel      Hotel  49.726242  19.003238   
16                      Hotel Gronie      Hotel  49.694671  18.986714   
17                    Hotel Dębowiec      Hotel  49.783062  19.025104   
18                      Hotel Sahara      Hotel  49.788860  19.030933   
19                      Beskidy Park      Hotel  49.778688  19.016084   
20      Schronisko PTTK Hala Miziowa      Hotel  49.540579  19.318637   
21                       Ventus Rosa      Hotel  49.820783  19.041999   
22          Schronisko PTTK Rysianka     Hostel  49.536463  19.234230   

                          id  
0   51bc4624498ef4bedaf74028  
1   4e67cb8dd22d12d83aeafabd  
2   4fed62d529a67907a7b05f06  
3   4bd892102ecdce7241d5d0f2  
4   4be1abb08dd062b52c773e3c  
5   4e43ecdc887703085fd98670  
6   4dd4f089813009ae1009518c  
7   50db3dcbe4b073c642e9ecb8  
8   4f7426b2e4b0fd5260f71c7a  
9   4f64c640e4b05c1d59a4cc5d  
10  4c1a15476a21c9b68674cb97  
11  4ed663dc77c88f53d78e660e  
12  5172c29e498e908f69047be9  
13  4fd0cccde4b0d89b24572697  
14  4be1abd68dd062b56f773e3c  
15  4be18e678dd062b51c563e3c  
16  5660c6fa498ea7ab991cb36a  
17  50f07ecde4b048abd4885b20  
18  4f749cefe4b07e69637499ad  
19  51b102f8498e5f78b1031b17  
20  4dc59973e4cd169dc65146b8  
21  511b4943e4b047cff83c3d95  
22  4e4110add22d6fdb87db2d9e

In [52]:
address = 'Żywiec, Poland' 

geolocator = Nominatim(user_agent="foursquare_agent")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Żywiec are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Żywiec are 49.6890338, 19.20305.


In [53]:
venues_map = folium.Map(location=[latitude, longitude], zoom_start=13) # generate map centred 

# add a red circle marker to represent the Conrad Hotel
folium.CircleMarker(
    [latitude, longitude],
    radius=5,
    color='red',
    popup='Żywiec',
    fill = True,
    fill_color = 'red',
    fill_opacity = 0.6
).add_to(venues_map)


# add markers to map
for lat, lng, name in zip(nearby_venues['lat'], nearby_venues['lng'], nearby_venues['name']):
    label = '{}, {}'.format(name, categories)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat,lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(venues_map)  
    
venues_map

## Explore the hotels further

### 1. Hotel & Spa Kocierz	

In [54]:
venue_id = '51bc4624498ef4bedaf74028' # Hotel & Spa Kocierz
url = 'https://api.foursquare.com/v2/venues/{}?client_id={}&client_secret={}&v={}'.format(venue_id, CLIENT_ID, CLIENT_SECRET, VERSION)
url

'https://api.foursquare.com/v2/venues/51bc4624498ef4bedaf74028?client_id=TJJA2JC1THEWW1AHB0YC4L24TWPQ4VDFOBHW0U3OEQ2MMXOR&client_secret=KMJPEOZNJQWE5PQRD20P2NKZYORRQDCKNTTFTOEAI5IMW4CO&v=20200803'

In [55]:
result = requests.get(url).json()
print(result['response']['venue'].keys())
result['response']['venue']

dict_keys(['id', 'name', 'contact', 'location', 'canonicalUrl', 'categories', 'verified', 'stats', 'likes', 'dislike', 'ok', 'rating', 'ratingColor', 'ratingSignals', 'allowMenuUrlEdit', 'beenHere', 'specials', 'photos', 'reasons', 'hereNow', 'createdAt', 'tips', 'shortUrl', 'timeZone', 'listed', 'seasonalHours', 'pageUpdates', 'inbox', 'attributes', 'bestPhoto'])


{'id': '51bc4624498ef4bedaf74028',
 'name': 'Hotel & Spa Kocierz',
 'contact': {},
 'location': {'address': 'ul. Beskidzka 206',
  'lat': 49.77846716198133,
  'lng': 19.31696445616376,
  'labeledLatLngs': [{'label': 'display',
    'lat': 49.77846716198133,
    'lng': 19.31696445616376}],
  'cc': 'PL',
  'city': 'Andrychów',
  'state': 'Województwo małopolskie',
  'country': 'Polska',
  'formattedAddress': ['ul. Beskidzka 206', 'Andrychów', 'Polska']},
 'canonicalUrl': 'https://foursquare.com/v/hotel--spa-kocierz/51bc4624498ef4bedaf74028',
 'categories': [{'id': '4bf58dd8d48988d1fa931735',
   'name': 'Hotel',
   'pluralName': 'Hotels',
   'shortName': 'Hotel',
   'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/travel/hotel_',
    'suffix': '.png'},
   'primary': True}],
 'verified': False,
 'stats': {'tipCount': 3},
 'likes': {'count': 9,
  'groups': [{'type': 'others',
    'count': 9,
    'items': [{'id': '404351889',
      'firstName': 'Maja',
      'lastName': 'M',
      '

In [56]:
try:
    print(result['response']['venue']['rating'])
except:
    print('This venue has not been rated yet.')

8.2


In [57]:
## lHotel & Spa Kocierz
limit = 15 # set limit to be greater than or equal to the total number of tips
url = 'https://api.foursquare.com/v2/venues/{}/tips?client_id={}&client_secret={}&v={}&limit={}'.format(venue_id, CLIENT_ID, CLIENT_SECRET, VERSION, limit)

results = requests.get(url).json()
results

#Get tips and list of associated features
tips = results['response']['tips']['items']

tip = results['response']['tips']['items'][0]
tip.keys()

#Format column width and display all tips
pd.set_option('display.max_colwidth', -1)

tips_df = json_normalize(tips) # json normalize tips

# columns to keep
filtered_columns = ['text', 'agreeCount', 'disagreeCount', 'id', 'user.firstName', 'user.lastName', 'user.gender', 'user.id']
tips_filtered = tips_df.loc[:, filtered_columns]

# display tips
tips_filtered

/opt/conda/envs/Python36/lib/python3.6/site-packages/pandas/core/indexing.py:1494: FutureWarning: 
Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate-loc-reindex-listlike
  return self._getitem_tuple(key)


text  \
0  Ok to tak - nie do końca żenada - do kolacji gra super góralska kapela, jedzenie pyszne night club fajny - trzeba to zrozumieć - mix spa i góralskiej chaty   

   agreeCount  disagreeCount                        id user.firstName  \
0  0           0              53afb3e1498e382b58178bfa  Krzysztof       

  user.lastName  user.gender   user.id  
0  K            NaN           58999301

### 2. Hotel Meta


In [58]:
venue_id = '4e67cb8dd22d12d83aeafabd' # Hotel Meta
url = 'https://api.foursquare.com/v2/venues/{}?client_id={}&client_secret={}&v={}'.format(venue_id, CLIENT_ID, CLIENT_SECRET, VERSION)

result = requests.get(url).json()
try:
    print(result['response']['venue']['rating'])
except:
    print('This venue has not been rated yet.')

7.8


In [59]:
## Hotel Meta

limit = 15 # set limit to be greater than or equal to the total number of tips
url = 'https://api.foursquare.com/v2/venues/{}/tips?client_id={}&client_secret={}&v={}&limit={}'.format(venue_id, CLIENT_ID, CLIENT_SECRET, VERSION, limit)

results = requests.get(url).json()
results

#Get tips and list of associated features
tips = results['response']['tips']['items']

tip = results['response']['tips']['items'][0]
tip.keys()

#Format column width and display all tips
pd.set_option('display.max_colwidth', -1)

tips_df = json_normalize(tips) # json normalize tips

# columns to keep
filtered_columns = ['text', 'agreeCount', 'disagreeCount', 'id', 'user.firstName', 'user.lastName', 'user.gender', 'user.id']
tips_filtered = tips_df.loc[:, filtered_columns]

# display tips
tips_filtered

text  \
0  niestety pokutuje dziwny polski obyczaj, że ryba to danie wegetariańskie -> obiadokolacje mają więc zazwyczaj jakąś rybę w ramach wege, czyli dla wegetarian zostają surówki z wkładką skrobiową :(   

   agreeCount  disagreeCount                        id user.firstName  \
0  0           0              56b74911498e21cc0b4d387a  Ewa             

  user.lastName  user.gender   user.id  
0  W            NaN           84591461

### 3. Hotel Zimnik

In [60]:
venue_id = '4dd4f089813009ae1009518c' # Hotel Zimnik
url = 'https://api.foursquare.com/v2/venues/{}?client_id={}&client_secret={}&v={}'.format(venue_id, CLIENT_ID, CLIENT_SECRET, VERSION)

result = requests.get(url).json()
try:
    print(result['response']['venue']['rating'])
except:
    print('This venue has not been rated yet.')


This venue has not been rated yet.


In [61]:
## hotel zimnik
limit = 15 # set limit to be greater than or equal to the total number of tips
url = 'https://api.foursquare.com/v2/venues/{}/tips?client_id={}&client_secret={}&v={}&limit={}'.format(venue_id, CLIENT_ID, CLIENT_SECRET, VERSION, limit)

results = requests.get(url).json()
results

#Get tips and list of associated features
tips = results['response']['tips']['items']

tip = results['response']['tips']['items'][0]
tip.keys()

#Format column width and display all tips
pd.set_option('display.max_colwidth', -1)

tips_df = json_normalize(tips) # json normalize tips

# columns to keep
filtered_columns = ['text', 'agreeCount', 'disagreeCount', 'id', 'user.firstName', 'user.lastName', 'user.gender', 'user.id']
tips_filtered = tips_df.loc[:, filtered_columns]

# display tips
tips_filtered

text  \
0  Combination of luxury, homely atmosphere and professional, competent service guarantees an excellent family holidays near montains, and lake. Order in restaurant regional and european cuisine!!!   

   agreeCount  disagreeCount                        id user.firstName  \
0  0           0              4dd4f445813009ae1009670d  Wojtek          

  user.lastName  user.gender  user.id  
0  W            NaN           9715468

## Based on the rating and positive comments the Hotel & Spa Kocierz was explored furter. In this search only the venues within 500m were explored.


# Hotel & Spa Kocierz


In [62]:
latitude = 49.778467
longitude = 19.316964
radius = 500
LIMIT=100
url = 'https://api.foursquare.com/v2/venues/search?&client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, radius, LIMIT)
url

'https://api.foursquare.com/v2/venues/search?&client_id=TJJA2JC1THEWW1AHB0YC4L24TWPQ4VDFOBHW0U3OEQ2MMXOR&client_secret=KMJPEOZNJQWE5PQRD20P2NKZYORRQDCKNTTFTOEAI5IMW4CO&ll=49.778467,19.316964&v=20200803&radius=500&limit=100'

In [63]:
import requests

In [64]:
results = requests.get(url).json()
'There are {} venues around Hotel & Spa Kocierz.'.format(len(results['response']['venues']))

'There are 100 venues around Hotel & Spa Kocierz.'

In [65]:
#results = requests.get(url).json()
#'There are {} venues around Hotel & Spa Kocierz.'.format(len(results['response']['groups'][0]['items']))

In [66]:
items = results['response']['venues']
venues[0]

{'reasons': {'count': 0,
  'items': [{'summary': 'This spot is popular',
    'type': 'general',
    'reasonName': 'globalInteractionReason'}]},
 'venue': {'id': '51bc4624498ef4bedaf74028',
  'name': 'Hotel & Spa Kocierz',
  'location': {'address': 'ul. Beskidzka 206',
   'lat': 49.77846716198133,
   'lng': 19.31696445616376,
   'labeledLatLngs': [{'label': 'display',
     'lat': 49.77846716198133,
     'lng': 19.31696445616376}],
   'distance': 12895,
   'cc': 'PL',
   'city': 'Andrychów',
   'state': 'Województwo małopolskie',
   'country': 'Polska',
   'formattedAddress': ['ul. Beskidzka 206', 'Andrychów', 'Polska']},
  'categories': [{'id': '4bf58dd8d48988d1fa931735',
    'name': 'Hotel',
    'pluralName': 'Hotels',
    'shortName': 'Hotel',
    'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/travel/hotel_',
     'suffix': '.png'},
    'primary': True}],
  'photos': {'count': 0, 'groups': []}},
 'referralId': 'e-0-51bc4624498ef4bedaf74028-0'}

In [67]:
# assign relevant part of JSON to venues
venues = results['response']['venues']

# tranform venues into a dataframe
dataframe = json_normalize(venues)
dataframe.head()

categories  \
0  [{'id': '4bf58dd8d48988d1fa931735', 'name': 'Hotel', 'pluralName': 'Hotels', 'shortName': 'Hotel', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/travel/hotel_', 'suffix': '.png'}, 'primary': True}]                       
1  [{'id': '4bf58dd8d48988d1c4941735', 'name': 'Restaurant', 'pluralName': 'Restaurants', 'shortName': 'Restaurant', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/default_', 'suffix': '.png'}, 'primary': True}]        
2  [{'id': '4bf58dd8d48988d1fa931735', 'name': 'Hotel', 'pluralName': 'Hotels', 'shortName': 'Hotel', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/travel/hotel_', 'suffix': '.png'}, 'primary': True}]                       
3  [{'id': '4eb1d4d54b900d56c88a45fc', 'name': 'Mountain', 'pluralName': 'Mountains', 'shortName': 'Mountain', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/parks_outdoors/mountain_', 'suffix': '.png'}, 'primary': True}]   
4  [{'id': '4bf58dd8d48988d15b941735', 'name': 'Farm', 'pluralName': 'Farms', 'shortName': 'Farm', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/parks_outdoors/farm_', 'suffix': '.png'}, 'primary': True}]                   

   hasPerk                        id           location.address location.cc  \
0  False    51bc4624498ef4bedaf74028  ul. Beskidzka 206          PL           
1  False    503f7814e4b010e25c790826  NaN                        PL           
2  False    4c1a15476a21c9b68674cb97  Taraganice, Beskidzka 206  PL           
3  False    52d9840c498ecf5c849047bc  NaN                        PL           
4  False    50049523e4b0bc5170c0bb07  NaN                        PL           

  location.city location.country location.crossStreet  location.distance  \
0  Andrychów     Polska           NaN                  0                   
1  NaN           Polska           NaN                  7                   
2  Andrychów     Polska           NaN                  17                  
3  NaN           Polska           NaN                  289                 
4  NaN           Polska           NaN                  8969                

                               location.formattedAddress  \
0  [ul. Beskidzka 206, Andrychów, Polska]                  
1  [Polska]                                                
2  [Taraganice, Beskidzka 206, 34-120 Andrychów, Polska]   
3  [Polska]                                                
4  [Polska]                                                

                                                       location.labeledLatLngs  \
0  [{'label': 'display', 'lat': 49.77846716198133, 'lng': 19.31696445616376}]    
1  [{'label': 'display', 'lat': 49.77850535353747, 'lng': 19.316884289875574}]   
2  [{'label': 'display', 'lat': 49.77831105265283, 'lng': 19.316908573392585}]   
3  [{'label': 'display', 'lat': 49.77702412699183, 'lng': 19.320316314697262}]   
4  [{'label': 'display', 'lat': 49.84416535349235, 'lng': 19.24467405419907}]    

   location.lat  location.lng location.postalCode           location.state  \
0  49.778467     19.316964     NaN                 Województwo małopolskie   
1  49.778505     19.316884     NaN                 NaN                       
2  49.778311     19.316909     34-120              Województwo małopolskie   
3  49.777024     19.320316     NaN                 NaN                       
4  49.844165     19.244674     NaN                 NaN                       

                  name    referralId venuePage.id  
0  Hotel & Spa Kocierz  v-1597710394  NaN          
1  Karczma Na Kocierzu  v-1597710394  NaN          
2  Kocierz Lodge & Spa  v-1597710394  NaN          
3  Przełęcz Kocierska   v-1597710394  NaN          
4  Czaniec              v-1597710394  NaN

In [68]:
# keep only columns that include venue name, and anything that is associated with location
filtered_columns = ['name', 'categories'] + [col for col in dataframe.columns if col.startswith('location.')] + ['id']
dataframe_filtered = dataframe.loc[:, filtered_columns]

# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

# filter the category for each row
dataframe_filtered['categories'] = dataframe_filtered.apply(get_category_type, axis=1)

# clean column names by keeping only last term
dataframe_filtered.columns = [column.split('.')[-1] for column in dataframe_filtered.columns]

dataframe_filtered

name  \
0   Hotel & Spa Kocierz                                    
1   Karczma Na Kocierzu                                    
2   Kocierz Lodge & Spa                                    
3   Przełęcz Kocierska                                     
4   Czaniec                                                
5   Kiczera                                                
6   BP                                                     
7   Panorama miasta                                        
8   Agroturystyka Maria                                    
9   Gora Zar                                               
10  PKL Góra Żar                                           
11  U Braci                                                
12  Rzyki                                                  
13  Nowak Mechanika Pojazdowa,  Stacja Kontroli Pojazdów   
14  all you can sleep                                      
15  Gniazdo Zmij                                           
16  Drukarnia Drukpress                                    
17  Zlota Rybca                                            
18  wyciąg czarny groń                                     
19  Plac Zabaw                                             
20  Hotel Elida                                            
21  Madohora holiday resort                                
22  Grzybobranie                                           
23  Sloneczny Stok                                         
24  Pub Trójka                                             
25  Poczta Polska                                          
26  Zajazd Pod Jeleniem                                    
27  Zajazd Skarpa                                          
28  Gala                                                   
29  Pod Baszta                                             
30  Andoria-Mot                                            
31  Hill                                                   
32  Doner King                                             
33  Piknik Nad Sołą                                        
34  Fanaberia                                              
35  Zespół Szkół Samorządowych w Sułkowicach Bolęcinie     
36  Sielska Dolina                                         
37  Bongo                                                  
38  Sami Swoi                                              
39  Hotel Żar                                              
40  U Joli                                                 
41  MDK Andrychów                                          
42  Pensjonat Rybak                                        
43  Cynamonowe Caffe                                       
44  Informacja Turystyczna                                 
45  DTL Sp. z o.o.                                         
46  Szyndzielnia                                           
47  Cmentarz komunalny                                     
48  Miami Tropic                                           
49  Na Wierchu                                             
50  zochuliny                                              
51  Glowing Cross                                          
52  Zajazd Rotunda                                         
53  DTL                                                    
54  U Zohuliny                                             
55  Samoobsługa                                            
56  Liceum Ogólnokształcące im. Marii Skłodowskiej-Curie   
57  Pizzeria La Cantina                                    
58  Kompleks wypoczynkowy Relaks                           
59  hill supermarket                                       
60  Targanice                                              
61  Spar                                                   
62  Chatka Gibasówka                                       
63  Jezioro Żywieckie                                      
64  Silesia                                                
65  Andrychów, Górnica                                     
66  Góra Żar                    

In [69]:
#### Let's visualize these items on the map around our location

In [70]:
venues_map = folium.Map(location=[latitude, longitude], zoom_start=15) # generate map centred around Hotel & Spa Kocierz


# add Hotel & Spa Kocierz as a red circle mark
folium.CircleMarker(
    [latitude, longitude],
    radius=10,
    popup='Hotel & Spa Kocierz',
    fill=True,
    color='red',
    fill_color='red',
    fill_opacity=0.6
    ).add_to(venues_map)


# add popular spots to the map as blue circle markers
for lat, lng, label in zip(dataframe_filtered.lat, dataframe_filtered.lng, dataframe_filtered.categories):
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        fill=True,
        color='blue',
        fill_color='blue',
        fill_opacity=0.6
        ).add_to(venues_map)

# display map
venues_map